## Oscillation in time and space with python: Reaction-Diffusion systems from scratch
### Why would you even want to code it anyway

Oscillating dynamic systems are fascinating! And omnipresent... No matter your background, you've probably come in contact with oscillators during your studies, be it in a form of an [RLC contour](https://en.wikipedia.org/wiki/RLC_circuit) in your electrical engineering class or in a form of a [circadian clock](https://en.wikipedia.org/wiki/Circadian_clock) in your biochemistry class.

[![Briggs–Rauscher reaction](https://upload.wikimedia.org/wikipedia/commons/thumb/8/8c/Briggs%E2%80%93Rauscher_reaction.webm/320px--Briggs%E2%80%93Rauscher_reaction.webm.jpg)](https://upload.wikimedia.org/wikipedia/commons/8/8c/Briggs%E2%80%93Rauscher_reaction.webm "Briggs–Rauscher reaction")
<body><center><font size="2"><br>[Briggs–Rauscher](https://en.wikipedia.org/wiki/Briggs%E2%80%93Rauscher_reaction) reaction  is a well-known chemical oscillator <br>(click on the image) </font></center></body>

Random question #1: what does the Briggs-Rauscher reaction in the video above has to do with the dotted pattern of cheetah and stripy pattern of zebra on the images below? Well, since this question is asked in the tutorial dedicated to oscillators, you might've guessed that the answer should have something to do with the oscillators... And this is indeed true. Although, if the Briggs-Rauscher reaction is an example of a system, that is periodic in time and is perfectly stable (homogenous) in space, the patterns on animal fur, quite the opposite, are examples of systems, that are periodic in space and perfectly stable in time. The idea, that initially homogenous systems can develop spatial patterns (periodicity in space), that stabilize with time, was discussed back in the 1952 by Alan Turing in [Chemical Basis of Morphogenesis](http://www.dna.caltech.edu/courses/cs191/paperscs191/turing.pdf). This seminal paper showed that the formation of many complex spatial patterns can be nicely described by all too familiar maths (and physics)! Which is really good news for anyone, who wants to recreate the formation of such patterns _in silico_.

<table>
<td>
<img width="250" height="150" src='images/Cheetah_pattern.jpg'></img>
<body><center><br>Stationary dotted pattern of cheetah ([img](https://upload.wikimedia.org/wikipedia/commons/6/68/Cheetah_%28Kruger_National_Park%2C_South_Africa%2C_2001%29.jpg))</center></body>
<td>
<td>
<img width="250" height="150" src='images/zebra_pattern.jpg'></img>
<body><center><br>Stationary stripy pattern of zebra ([img](https://upload.wikimedia.org/wikipedia/commons/1/12/Hartmann_zebra_hobatere_S.jpg))</center></body>
<td>
</table>

Now you might be thinking: ok, I can picture systems, that are periodic in time and stable (homogenous) in space - they behave like chemical oscillators in a well-stirred beaker; I can also picture systems that are periodic in space and stable in time - these are the systems, that, e.g., describe the formation of patterns on animal fur. But what about the systems that are periodic in both time and space? That's a great thing to wonder about, as diversity of patterns and complexity of behaviours, emerging in such systems, is mind-boggling! In literature you would usually find mentions of spirals, standing waves and packet waves, which often emerge in such systems. In physical world these patterns occur, e.g., in a petri dish with [Belousov-Zhabotinsky](https://en.wikipedia.org/wiki/Belousov%E2%80%93Zhabotinsky_reaction) reaction. But there's so much more to it! In autocatacytic Reaction-Diffusion system described by the Gray-Scott model you can stumble upon dynamic patterns that resemble cell division, coral growth and even the formation of exotic [U-skates](http://mrob.com/pub/comp/xmorphia/uskate-world.html)! Robert Munafo's [xmorphia](http://mrob.com/pub/comp/xmorphia/index.html) is a great resource to explore all the bizzare patterns that emerge in Gray-Scott system. Here are some examples:

<table>
<td>
    <img src='https://upload.wikimedia.org/wikipedia/commons/d/d9/The_Belousov-Zhabotinsky_Reaction.gif' style="width:200px;height:200px;"></img>
    <body><center> <br>Spirals in <br> [Belousov-Zhabotinsky](https://en.wikipedia.org/wiki/Belousov%E2%80%93Zhabotinsky_reaction) reaction</center> </body>
<td>    

<td>
<img src='https://j.gifs.com/MQG2RR.gif' style="width:200px;height:200px;"></img>
<body><center><br>"Cell division" and "coral growth" <br>in Gray-Scott Reaction-Diffusion system ([vid](https://www.youtube.com/watch?v=PtPK_xx5Hks))</center></body>
<td>
    
<td>
    <img src='https://j.gifs.com/oQ1KOY.gif' style="width:300px;height:200px;"></img>    
    <body><center> "U-skates" emerging <br>in Gray-Scott Reaction-Diffusion system ([vid](http://mrob.com/pub/comp/xmorphia/index.html#formula))</center></body>
<td>
</table>

In this tutorial we will NOT explore all the complexity of the emergent behaviour in Reaction-Diffusion systems. Instead we will learn how to set up such systems from scratch in python and how to systematically search for interesting patterns. I will just go ahead and assume that most people reading this are curious about the topic, but hadn't had a proper time to explore it yet; so you probably still remember some bits and pieces from Calculus and Linear Algebra, but wouldn't mind a recap. Of course, if you feel you're well versed in both, feel free to skip the recap-sections. Ok, here goes!

><font size=2>
  In this notebook we'll be working with two system representations: "physical" and [state-space](https://en.wikipedia.org/wiki/State-space_representation). Physical representation uses notation familiar from textbooks, so we'll use this representation when initially working out the equations (e.g., we'll use $c$ for concentrations/expression levels and $k$ for reaction rate coefficients). State-space representation abstracts away from any physical meaning, which obfuscates things a little, but at the same time makes it more convenient to use general-purpose math tools. We'll mostly use state space notation in the code (e.g., we'll use $x$ to denote system state variables, $u$ to denote external inputs and $p$ to denote system parameters)</font>. 


In [1]:
from PIL import Image
import numpy as np

import matplotlib.pyplot as plt
import matplotlib.patches as mpatches

from bokeh.plotting import figure
from bokeh.io import push_notebook, show, output_notebook
from bokeh.models import ColumnDataSource
from bokeh.models.widgets import Div
from bokeh.layouts import row, column
from bokeh.palettes import Colorblind
from  ipywidgets import interact
output_notebook()

from recaps.utils import eulerForward, rungeKutta2, get_dynamic_plots, diffuse, convert2img

Loading BokehJS ...

Loading BokehJS ...

### Few words on setting up (partial) differential equations

Systems that change over time are classically described by differential equations. These equations reflect conservation of some property of a system: at any point in time all the stuff that goes into the box must go out of the box, it doesn't spontaneously emerge or disappear into the void. Simple. 

_Ok, what if it doesn't disappear, but is just converted into "other stuff" in some sort of reaction?_ 

Fine, at any point in time all the stuff that goes into the box must balance out the stuff that goes out of the box and reacts away inside the box (also, for general accounting purposes, we should write a similar balance for the "other stuff", which is now generated inside the box). 

_Ok ok, but what if the box has a capacity to build up and release some reserve of stuff?_ 

Fine! Any stuff that comes in and is not balanced out by going out and reacting away, is accumulated inside the box!

<img src="images/setting_up_the_balance.png" style="width:770px;height:270px;"></img>

_Better. But what's this! Concentration of stuff is the same everywhere in the box? This might be acceptable to describe a chemical reaction in a well-stirred beaker, but what about all those nonhomogenous systems?_ 

Easy. We'll just pretend that our box is composed of several smaller compartments connected in series. Concentration of stuff inside each compartment can be homogenous, but, as long as the number of such compartments is sufficiently high, this __tanks-is-series__ model should approximate the original system well. Ideally we'd want to approximate our system by the series of infinitely many infinitesimal compartments. Such system would be described by a __partial differential equation (pde)__, where concentration $c$ depends both on time $t$ and coordinate $x$. Of course for practical purposes we'll __discretize__ the system into finite number of compartments and treat the concentration in each compartment $c_{i}$ as an individual variable, which depends only on time $t$:   

<img src="images/setting_up_the_pfr_balance_hor.png" style="width:850px;height:250px;"></img>

_Better, but still not perfect. Now all the stuff is always moving in the same direction - there's no back mixing... This model might be acceptable to describe the flow of water through long narrow pipes, but there's no way we can use it to describe the growth of bacteria in a petri dish, where stuff diffuses in all directions... _

Ok, __diffusion__ is a bit trickier. Stuff, as expected, diffuses to locations, where its concentration is lower. More specifically, diffusive [flux](https://en.wikipedia.org/wiki/Flux) is driven by a concentration gradient - change in concentration per unit of distance ($-\frac{dc}{dx}$) for those living in a 1D world, or per unit of space ($-\nabla{c}$) for everyone else ($\nabla$ - is [nabla](https://en.wikipedia.org/wiki/Nabla_symbol) operator; "$-$" sign because the flux is _positive_ in the direction along which the concentration _decreases_). If we choose $D$ to be some proportionality constant, characteristic for our stuff and environment through which it diffuses, then we can write the expression for the diffusive flux as:

$$ J = -D \frac{dc}{dx} \rightarrow J = -D \nabla{c}$$

Flux tells us something about the __direction__ of diffusion, but doesn't tell anything about its __rate__. To get the expression for the rate of concentration change at any point in space, we can speculate, that if there is no chemical reaction, the change of concentration can only be due to flux, so $ \frac{\partial c}{\partial t} + \frac{\partial J}{\partial x} = 0$. If we combine it with the expression for flux, we'll get the proper expression for the diffusion rate, also known as [second Fick's law](https://en.wikipedia.org/wiki/Fick%27s_laws_of_diffusion) of diffusion:

$$ \frac{\partial c}{\partial t} = D\frac{\partial^2 c}{\partial x^2} \rightarrow \frac{\partial c}{\partial t} = D\nabla^2{c}$$


The only thing left to do now is to figure out how we can adjust this expression to account for reaction. Well, if there _is_ a reaction, then the change of concentration of stuff at any point in space can be explained both by its diffusion from one point to another _and_ by its reaction to "another stuff". So we can just _add_ the reaction term to the Fick's law, taking care of the units:

<img width="700" height="550" src="images/reaction-diffusion.png"></img>

Remember that in 1D second order derivative is just a "gradient of a gradient", so in discretized form we can write it as $(\frac{\Delta c_{i+1}}{\Delta x} - \frac{\Delta c_{i}}{\Delta x})/\Delta x$. This 1D discretization  nicely shows, how diffusion term mathematically "smoothens" the concentration values over the neighbouring compartments: 

<img width="600" height="55" src="images/fick_discretization_full.png"></img>

You might imagine that this effect can be quite handy for blurring out the noise in the images. And indeed, the exact same equation (although usually referred to as "heat equation") is used in image processing as a simple blurring tool. You just need to treat the RGB channels of an image as 2D concentration maps of some chemical species. 

Here is what adding diffusion to an image looks like:


In [5]:
%%HTML 
<video height="300" width="400" controls><source src="images/img_diffusion.mp4"></video>

><font size=2> [Why this image](https://en.wikipedia.org/wiki/Lenna)?</font>

And by adding the reaction you can make things a bit more... psychedelic... Here I added the reaction, in which red, green and blue colors behave like species in predator-prey system: red preys on green, green preys on blue, and blue preys on red:

In [6]:
%%HTML 
<video height="300" width="400" controls><source src="images/img_reaction_diffusion.mp4"></video>

><font size=2>[This](img_processing_example.ipynb) notebook explains how to generate these animations. Don't worry if you don't understnand much yet: in the next sections we'll go through all the topics in more detail.</font>

### And now we'll learn to do the same thing the right way...

In general, the reaction-diffusion pde, that we saw in the previous section, can equally well describe homogeneous systems that oscillate in time (systems with Hopf bifurcation), inhomogenous steady systems (systems with Turing bifurcation), as well as inhomogenous oscillating systems. So what regulates the behaviour and determines the patterns? Well, the ability to accomodate various patterns depends on complexity of the reaction term, which we were unrightfully ignoring so far (we'll get there!); but the exact pattern and behaviour depend on system parameters. 

Soo... if we select the reations and set the parameters, we can simulate the system and check how it behaves. But can we _predict_ this behaviour _without_ simulation? Just from looking at the parameters? And, more importantly, if we're interested in a very particular behaviour, is there a way to pick the corresponding parameters without checking each and every combination, untill we finally hit the right one? The answer is _sort of_: we can't determine which parameters in Gray-Scott system will lead to the formation of ["U-skates"](http://mrob.com/pub/comp/xmorphia/uskate-world.html), but we can map the regions with different types of bifurcation in parameter space. This would be the part, where we'll need to remember the Linear Algebra. But before we start remembering, let's just play around with the simpler systems and try to build up some intuition first.


### Simple homogeneous oscillators

Let's forget about the diffusion for a moment, and pretend that we have a homogeneous system. Suppose that we have two gens in our system: $A$ inhibits $B$ and $B$ activates $A$. To keep things simple let's assume linear relation between the expression _rates_ ($\frac{dc_{A}}{dt}$ and $\frac{dc_{B}}{dt}$) and expression _levels_ ($c_{A}$ and $c_{B}$):

<img width="300" height="50" src="images/ode_simple_oscillator.png"></img>

Let's check how the system would behave if we vary parameters $k_{AB}$ and $k_{BA}$. First we'll solve this system numerically using second order Runge-Kutta method for integration.

><font size=2>Quick recap: [numerical solutions of ordinary differential equations](recaps/numerical_solutions_recap.ipynb)</font>


In [3]:
# ---define the system---
# mass balance: all we know about the system is stored here
def balances(_, x, p):
    """dc_a/dt =  k_ba*c_b
       dc_b/dt = -k_ab*c_a"""     
    k_ba, k_ab, x_a, x_b = p[0], -p[1], x[0], x[1]
   
    return np.array([ k_ba * x_b,  # dc_a/dt
                     -k_ab * x_a]) # dc_b/dt

# initial condition
x0 = np.array([0.5,  # c_a(t=0)
               0.5]) # c_b(t=0)

# time related
t0,dt,tf = 0,0.001,50
t_span = np.arange(t0,tf+dt,dt)

# parameters
p = [ 0.5, # k_ba
     -0.5] #-k_ab   


In [4]:
# ---set up solver (Runge Kutta 2)---
def rungeKutta2(dxdt, x, t_span, p):
    dt = t_span[1] - t_span[0] # get dt
    x = x.astype(float) 
    
    # preallocate/initialize
    x_span = np.zeros((len(x), len(t_span)+1))
    x_span[:,0] = x
    
    for it,t in enumerate(t_span):
        k1 = dxdt(t,        x,        p)*dt
        k2 = dxdt(t+0.5*dt, x+0.5*k1, p)*dt
        x += k2
        x_span[:,it+1] = x
        
    return x_span[:,:-1]# on each iter we calculate x for the next step, so at the end we'll have one extra x  
        

In [5]:
# ---plot stuff!---
x_num = rungeKutta2(balances, x0, t_span, p)
title = "simple homogeneous oscillator"
labels = ["time", "expression level"]
legend = ["expression level of A", "expression level of B"]
comment = "<br>Perhaps assuming linear relation\
           between expression rates and expression levels\
           wasn't a great idea - <br>\
           now our system has genes with negative expression... fantastic...<br><br>\
           We can fix it by assuming more realistic \
           nonlinear kinetics, \
           but let's not do it just yet. \
           After all, we're only trying to build intuition\
           while playing with simple maths here."

def get_dynamic_plots(t_span, x_num, title, labels, legend, comment=""):
    # plot states as functions of time
    y_min, y_max = min(x_num.ravel()), max(x_num.ravel())
    plt1 = figure(title=title, 
                  x_range=[t_span[0], t_span[-1]], 
                  y_range=[y_min - 0.3*(y_max-y_min), y_max + 0.3*(y_max-y_min)],
                  plot_width=450, plot_height=250)
    plt1.xaxis.axis_label = labels[0]
    plt1.yaxis.axis_label = labels[1]
    
    colors = Colorblind[max(len(x_num), min(Colorblind.keys()))]
    r1 = [plt1.line(t_span, x_num[i,:], color=colors[i], line_width=2, legend=legend[i])
          for i in range(len(x_num))]
    
    # plot x2 as a functino of x1
    x_min, x_max, y_min, y_max = min(x_num[0,:]), max(x_num[0,:]), min(x_num[1,:]), max(x_num[1,:])
    plt2 = figure(x_range=[x_min - 0.3*(x_max-x_min), x_max + 0.3*(x_max-x_min)],
                  y_range=[y_min - 0.3*(y_max-y_min), y_max + 0.3*(y_max-y_min)],
                  plot_width=250, plot_height=250)
    plt2.xaxis.axis_label = legend[0]
    plt2.yaxis.axis_label = legend[1]
    r2 = plt2.line(x_num[0,:], x_num[1,:], color=colors[0], line_width=2)

    div = Div(width=250, text=comment)

    show(row(plt1, plt2, div), notebook_handle=True)    
    return plt1, plt2, r1, r2

plt1, plt2, r1, r2 = get_dynamic_plots(t_span, x_num, title, labels, legend, comment=comment)   


# add interactive sliders to check the effect of parameters and dt
def update(p_ab=0.25, p_ba=-0.25, dt=0.05):
    t = np.arange(t0,tf+dt,dt)
    c_a, c_b = rungeKutta2(balances, x0, t, [p_ba, p_ab])
    
    r1[0].data_source.data = {'x': t,   'y': c_a}
    r1[1].data_source.data = {'x': t,   'y': c_b}
    r2.data_source.data  = {'x': c_a, 'y': c_b}
    push_notebook()

interact(update, p_ab=(-1,1,0.005), p_ba=(-1,1,0.005), dt=(0.05,2,0.05))


interactive(children=(FloatSlider(value=0.25, description='p_ab', max=1.0, min=-1.0, step=0.005), FloatSlider(value=-0.25, description='p_ba', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.05, description='dt', max=2.0, min=0.05, step=0.05), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

This system happens to oscillate, whenever two parameters ($k_{AB}$ and $k_{BA}$) have opposite signs (when one gene acts as activator and the other - as inhibitor). And when two parameters have the same signs (so we have either two activators or two inhibitors) the system "explodes"... That's not particularly interesting... So  let's make a small correction: suppose $A$ expression can now be inhibited by its own high levels:

<img width="400" height="50" src="images/ode_simple_oscillator_with_inhibition.png"></img>

In [6]:
def balances(_, x, p):
    """dc_a/dt = -k_aa*c_a + k_ba*c_b
       dc_b/dt = -k_ab*c_a           """ 
    k_aa, k_ba, k_ab, c_a, c_b = -p[0], p[1], -p[2], x[0], x[1]
    
    return np.array([-k_aa*c_a + k_ba*c_b,
                     -k_ab*c_a])

p = [-0.10, # k_aa
      0.25, # k_ba
     -0.25] # k_ab

# ---plot stuff!---
x_num = rungeKutta2(balances, x0, t_span, p)

show(row(plt1, plt2), notebook_handle=True)

# add interactive sliders to check the effect of parameters and dt
def update(p_aa=-0.10, p_ab=0.25, p_ba=-0.25, dt=0.05):
    t = np.arange(t0,tf+dt,dt)
    c_a, c_b = rungeKutta2(balances, x0, t, [p_aa, p_ba, p_ab])
    
    r1[0].data_source.data = {'x': t,   'y': c_a}
    r1[1].data_source.data = {'x': t,   'y': c_b}
    r2.data_source.data  = {'x': c_a, 'y': c_b}
    push_notebook()

interact(update, p_aa=(-1,1,0.005), p_ab=(-1,1,0.005), p_ba=(-1,1,0.005), dt=(0.05,2,0.05))
    

interactive(children=(FloatSlider(value=-0.1, description='p_aa', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.25, description='p_ab', max=1.0, min=-1.0, step=0.005), FloatSlider(value=-0.25, description='p_ba', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.05, description='dt', max=2.0, min=0.05, step=0.05), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

Ooh, by introducing self-inhibition ($k_{AA} c_A$ term) we got ourselves a damper! Now we can regulate whether or when the system reaches stable steady state. 

One thing we can still check, is the effect of self-activation/inhibition of $B$. By now you can probably figure out yourself, what needs to be changed in the code, to account for this process. So just go ahead - modify the code above and check how this process affects system's behaviour.

### What does Linear Algebra have to do with any of this

Toggling the parameters is fun, but it's definitely not the most systematic way of analyzing the system (imagine doing it for complex systems with large number of parameters). We can do better. Luckily, since our system is linear, we can unleash all the tools that Linear Algebra has to offer (and that's a lot)! To see what we can do, let's first rewrite the system in a more Linear-Algebra-compliant (and somewhat cleaner) form:

$$ \begin{cases} \frac{dx_{A}}{dt} = -k_{AA}x_{A} + k_{BA}x_{B} \\
                 \frac{dx_{B}}{dt} = -k_{AB}x_{A} \end{cases} \rightarrow
   \begin{cases} \frac{dx_{A}}{dt} = -k_{AA}x_{A} + k_{BA}x_{B} \\
                 \frac{dx_{B}}{dt} = -k_{AB}x_{A} + 0\cdot x_{B} \end{cases} \rightarrow
   \begin{bmatrix} \frac{dx_{A}}{dt} \\ \frac{dx_{B}}{dt} \end{bmatrix} = 
   \begin{bmatrix} -k_{AA} & k_{BA} \\ -k_{AB} & 0 \end{bmatrix} \cdot 
   \begin{bmatrix} x_{A} \\ x_{B} \end{bmatrix} \rightarrow 
   \dot{\textbf{x}} = \textbf{A} \textbf{x} $$
   
where $\dot{\textbf{x}} = \begin{bmatrix} \frac{dx_{A}}{dt} \\ \frac{dx_{B}}{dt} \end{bmatrix}$, 
      $\textbf{x} = \begin{bmatrix} x_{A} \\ x_{B} \end{bmatrix}$ and
      $\textbf{A} = \begin{bmatrix} -k_{AA} & k_{BA} \\ -k_{AB} & 0 \end{bmatrix}$.
      
><font size=2>
 The $\textbf{A}$ matrix (not to be confused with gene $A$) is called the _state matrix_, because it transforms the _state vector_ $\textbf{x}$. But you could've also recognized it as [Jacobian](https://en.wikipedia.org/wiki/Jacobian_matrix_and_determinant), as it is composed of first order partial derivatives of the ode's with respect to each of the states. </font>

Since our system of ode's is linear and doesn't have any input terms, its analytical solution should have a form $\textbf{x} = \textbf{v}e^{\lambda t}$. The main question is, how do we find $\textbf{v}$ and $\lambda$... Let's plug in this generic candidate solution into the system definition:

$$ \dot{\textbf{x}} = \textbf{A} \textbf{x} \rightarrow 
   \lambda \textbf{v} e^{\lambda t} = \textbf{A} \textbf{v}e^{\lambda t} \rightarrow 
   \lambda \textbf{v} = \textbf{A} \textbf{v} $$
   
Dis you recognize the last expression? It's the textbook definition of [eigenvalues and eigenvectors](https://en.wikipedia.org/wiki/Eigenvalues_and_eigenvectors)! For us it means that $\textbf{x} = \textbf{v}e^{\lambda t}$ can only be solution of system $\dot{\textbf{x}} = \textbf{A} \textbf{x}$ if $\textbf{v}$ is the eigenvector of $\textbf{A}$ and $\lambda$ is the corresponding eigenvalue.      
      

In [7]:
A = np.array([[-0.10, 0.25],
              [-0.25, 0   ]])
eigval, eigvec = np.linalg.eig(A)

print('\neigenvalues: \n{}'.format(eigval))
print('\neigenvectors: \n{}'.format(eigvec))


eigenvalues: 
[-0.05+0.24494897j -0.05-0.24494897j]

eigenvectors: 
[[0.70710678+0.j         0.70710678-0.j        ]
 [0.14142136+0.69282032j 0.14142136-0.69282032j]]


Oh, for 2x2 matrix there are two eigenvalues and two eigenvectors... Which ones do we choose? Well, both. Since our system is linear, the [linear combination](https://en.wikipedia.org/wiki/Linear_combination) (weighted sum) of its solutions would also be a solution. So the general solution would look something like: 

$$ \textbf{x} = \alpha \textbf{v}_{1}e^{\lambda_1 t} + \beta \textbf{v}_{2}e^{\lambda_2 t}$$ 

where $\alpha$ and $\beta$ are some coefficients, that can be found as long as we know the state of the system $\textbf{x}$ at $t=0$:

$$ \textbf{x}_0 = \alpha \textbf{v}_{1}e^{\lambda_1 \cdot 0} + \beta \textbf{v}_{2}e^{\lambda_2 \cdot 0} = \
   \alpha\textbf{v}_1 + \beta \textbf{v}_2 = \
   \begin{bmatrix} \textbf{v}_1 & \textbf{v}_2 \end{bmatrix} \cdot \begin{bmatrix} \alpha \\ \beta \end{bmatrix}$$

In [9]:
coef = np.linalg.solve(eigvec, x0)
print('coefficients: \n{} \n{}'.format(coef[0], coef[1]))

coefficients: 
(0.35355339059327384-0.28867513459481287j) 
(0.35355339059327384+0.28867513459481287j)


In [10]:
# confirm if these coefficients indeed solve x0 = eigvec.coef
np.allclose(np.dot(eigvec, coef), x0)

True

By the way, did you notice that the calculated eigenvalues are complex? What does it mean for the ode solution? Remember that the solution for each state $x$ would have a general form $\text{constant} \cdot e^{\lambda t}$. If lambda is complex, we can write:

<center><br>
$ x = 
  \text{const} \cdot e^{\lambda t} = 
  \text{const} \cdot exp\big($ <font color="teal">$Re(\lambda t)$</font> + <font color="indianred">$i\text{ }Im(\lambda t)$    </font> $\big) = \
  \text{const} \cdot $ <font color="teal">$e ^{Re(\lambda t)}$</font> <font color="indianred">$e^{i \text{ } Im(\lambda t)} $</font> 
  $ = \text{const} \cdot$ 
  <font color="teal">$ e^{Re(\lambda t)}$</font>
  <font color="indianred">$\big(cos(Im(\lambda t)) + i\text{ } sin(Im(\lambda t))\big)$</font></center>

><font size=2>Here we used [Euler's formula](https://en.wikipedia.org/wiki/Euler%27s_formula):</font>
><img width="250" height="400" src="images\complex_numbers.png"></img>

It appears that the <font color="indianred">imaginary</font> part of the eigenvalue $\lambda$ is responsible for all the oscillations (if $Im(\lambda t)$ is 0, the whole <font color="indianred">reddish</font> part reduces to $1$ and all the sines and cosines disappear)! And the <font color="teal">real</font> part of $\lambda$ is responsible for modulating the amplitude of these oscillations: if $Re(\lambda t)$ is positive, then the amplitude of the oscillations increases with time and the system "explodes"; and if $Re(\lambda t)$ is negative, the oscillations gradually dampen, and the system converges to stable steady-state. (Can you see what would happen if $Re(\lambda t) = 0$?) 

For us this means, that just by varying the parameters and checking the eigenvalues of the resulting $\textbf{A}$-matrix, we can map system behaviour in parameter space without running any simulations!


In [11]:
p_aa_span, p_ba_span = np.linspace(-1,1,201), np.linspace(-1,1,201)
values   = [[None for _ in range(len(p_ba_span))] for _ in range(len(p_aa_span))]
patterns = [[None for _ in range(len(p_ba_span))] for _ in range(len(p_aa_span))]

# check the eigenvalues for each combination of p_aa and p_ba in given ranges
for ip_aa,p_aa in enumerate(p_aa_span):
    for ip_ba,p_ba in enumerate(p_ba_span):
        A[0,0] = p_aa
        A[0,1] = p_ba
    
        eigval,_ = np.linalg.eig(A)
        
        # yes oscillations
        if np.imag(eigval[0]) or np.imag(eigval[1]): 
            # exploding (undamped)
            if np.real(eigval[0]) > 0 or np.real(eigval[1]) > 0: 
                values[ip_aa][ip_ba] = 0.75
                patterns[ip_aa][ip_ba] = "'exploding' oscillations"
            # periodic -> Hopf bifurcation(critically damped)
            elif np.real(eigval[0]) == 0 and np.real(eigval[1]) == 0:
                values[ip_aa][ip_ba] = 0.5
                patterns[ip_aa][ip_ba] = "periodic oscillations"
            # decaying (subcritically damped -> stable steady-state)
            else:             
                values[ip_aa][ip_ba] = 0.25
                patterns[ip_aa][ip_ba] = "decaying oscillations"
        # no oscillations
        else:
            # exploding
            if eigval[0] > 0 or eigval[1] > 0:
                values[ip_aa][ip_ba] = 1
                patterns[ip_aa][ip_ba] = "'exploding'"
            # stable steady-state
            else:
                values[ip_aa][ip_ba] = 0
                patterns[ip_aa][ip_ba] = "decaying"

data = dict(image=[values],
            pattern=[patterns])

# ---plot stuff!---
# get pattern map
plt3 = figure(x_range=(p_ba_span[0], p_ba_span[-1]),
              y_range=(p_aa_span[0], p_aa_span[-1]),
              plot_width=250, plot_height=250,
              tooltips=[("p_aa", "$y"), ("p_ba", "$x"), ("pattern", "@pattern")],
              title="mouse over the regions")

plt3.image(source=data, image='image', x=-1, y=-1, dw=2, dh=2, palette="Greys256")
plt3.xaxis.axis_label = "p_ba"
plt3.yaxis.axis_label = "p_aa"

# show dynamic plot and pattern map
div = Div(width=210,
          text="""<br>Simulate the system (use sliders) to confirm that the patterns, \
                  mapped by analyzing the eigenvlues, were identified correctly.""")
show(row(plt1, plt3, div), notebook_handle=True)

# add interactive sliders to check the effect of parameters and dt
def update(p_aa=-0.10, p_ba=0.25):
    t = np.arange(0, tf+0.05, 0.05)
    c_a, c_b = rungeKutta2(balances, x0, t, [p_aa, p_ba, -0.25])
    
    r1[0].data_source.data = {'x': t,   'y': c_a}
    r1[1].data_source.data = {'x': t,   'y': c_b}
    push_notebook()

interact(update, p_aa=(-1,1,0.005), p_ba=(-1,1,0.005))              

interactive(children=(FloatSlider(value=-0.1, description='p_aa', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.25, description='p_ba', max=1.0, min=-1.0, step=0.005), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

### How do we extend this for nonlinear systems?

Eigenvalues told us a lot about the patterns in system behaviour... Sorry, eigenvalues told us a lot about the patterns in __linear__ system behaviour (various steps of our analysis relied on the assumption, that we're dealing with linear system). Well, that's a bit meh, since, if we're looking for "interesting" patterns, we should probably look into complex nonlinear systems. Is there _any_ way we can apply what we've learned about eigenvalues to map the behaviour of nonlinear systems?

Turns out there is a way! And it involves __linearization__ of the nonlinear system. Linearization doesn't mean that we magically replace the nonlinear system with its linear analog without any loss of information. The system can only be linearized __locally__: just like any complex curve can be approximated by a straight line _in a proximity of some point_ if we zoom-in close enought, - any system of nonlinear ode's can also be approximated by a system of linear ode's _in a proximity of some point_. Which point? A decent choice is "some point in time veeery far from now", because often we're only interested in knowing how the system would behave "in the end": will it explode or will it stabilize? Formally "in the end" means "at the steady state", which is the same as "when all the changes cease" or $\frac{d\textbf{x}}{dt} = 0$. 

To make it sound less abstract, let's work out an example. Let's look at the classical predator-prey system, that the undergrads are introduced to during their Calculus class. We can assume that we have a closed (no inputs, no outputs) homogeneous system, where prey grows on some mysterious unlimited food source at a rate proportional to its population density $\mu x_{prey}$, and predators gradually die out at a rate proportional to their population density $b x_{pred}$. When predator encounters prey, some fraction of prey's mass ($Y$) is converted into predator's mass. The rate of predator-prey encounters should be proportional to probability of both predator and prey being at the same time at the same place: $kx_{pred}x_{prey}$. Then we can write:

<img width="750" height="70" src="images/ode_pred_prey.png"></img>

><font size=2>Does this look like autocatalytic chemical reaction? It definitely looks like autocatalitic chemical reaction.</font>

What would be the population densities of predator and prey at the steady state ($x^{*}_{pred}$ and $x^{*}_{prey}$)? 

$$ \begin{cases} \frac{dx_{prey}}{dt} = 0 \\ \frac{dx_{pred}}{dt} = 0 \end{cases} \rightarrow 
   \begin{cases} \mu x^{*}_{prey} - \frac{k}{Y} x^{*}_{prey}x^{*}_{pred} = 0 \\ 
                 k x^{*}_{prey}x^{*}_{pred} - b x^{*}_{pred} = 0 \end{cases} $$
   
With some high-school algebra we can find $x^{*}_{prey} = \frac{b}{k} $ and $x^{*}_{pred} =  \frac{\mu y}{k} $ (alternatively, we can be a bit lazy and [estimate $x^{*}_{prey}$ and $x^{*}_{pred}$ numerically](recaps/newton_method.ipynb) using, e.g., [Newton's method](https://en.wikipedia.org/wiki/Newton%27s_method)). Great! Now what...


To carry out the same kind of analysis that we've done for the linear system, we need to rewrite our new system in the form $\dot{\textbf{x}} = \textbf{A} \textbf{x}$. Let's recall that $\textbf{A}$-matrix is a [Jacobian](https://en.wikipedia.org/wiki/Jacobian_matrix_and_determinant), so we can still find it for nonlinear system: 

$$ \begin{bmatrix} \frac{dx_{prey}}{dt} \\ \frac{dx_{pred}}{dt} \end{bmatrix} = 
   \begin{bmatrix} \frac{\partial(\mu x_{prey} - \frac{k}{Y} x_{prey}x_{pred})}{\partial{x_{prey}}} & 
                   \frac{\partial(\mu x_{prey} - \frac{k}{Y} x_{prey}x_{pred})}{\partial{x_{pred}}} \\ 
                   \frac{\partial(k x_{prey}x_{pred} - b x_{pred})}{\partial{x_{prey}}} & 
                   \frac{\partial(k x_{prey}x_{pred} - b x_{pred})}{\partial{x_{pred}}} \end{bmatrix} \cdot 
   \begin{bmatrix} x_{prey} \\ x_{pred} \end{bmatrix} \rightarrow 
   \begin{bmatrix} \frac{dx_{prey}}{dt} \\ \frac{dx_{pred}}{dt} \end{bmatrix} = 
   \begin{bmatrix} \mu - \frac{k}{Y} x_{pred} & -\frac{k}{Y} x_{prey} \\
                   k x_{pred} & k x_{prey} - b \end{bmatrix} \cdot 
   \begin{bmatrix} x_{prey} \\ x_{pred} \end{bmatrix} \rightarrow
   \dot{\textbf{x}} = \textbf{A} \textbf{x} $$ 
   
where $\textbf{A} = \begin{bmatrix} \mu - \frac{k}{Y} x_{pred} & -\frac{k}{Y} x_{prey} \\ k x_{pred} & k x_{prey} - b \end{bmatrix}$ varies with time, as states $x_{prey}$ and $x_{pred}$ vary with time. Luckily we've already decided, that we're only interested in system behaviour at the steady state, where $\textbf{A}$-matrix becomes linearized 
$ \textbf{A}^{*} = \begin{bmatrix} \mu - \frac{k}{Y} x^{*}_{pred} & -\frac{k}{Y} x^{*}_{prey} \\ 
                                   k x^{*}_{pred} & k x^{*}_{prey} - b \end{bmatrix}$.
                                   
The rest is straightforward: we plug in $x^{*}_{prey} = \frac{b}{k} $ and $x^{*}_{pred} =  \frac{\mu y}{k} $, calculate eigenvalues of $\textbf{A}^{*}$ and find out, that... no matter which _physically justifiable_ parameter values we choose, the system will _always_ bifurcate (prove it)! Let's confirm it with simulations and move on.


In [13]:
def balances_pred_prey(_, x, p):
    prey, pred = x[0], x[1]
    return np.array([p['mu']*prey - p['k']/p['y']*prey*pred,
                     p['k']*prey*pred - p['b']*pred])

# time related
t0,dt,tf = 0,0.001,50
t_span = np.arange(t0,tf+dt,dt)

# initial conditions
x0 = np.array([1., # prey0
               1.])# pred0
# parameters
p = {'mu': 0.8,  # growth rate of prey
     'k' : 0.2,  # success rate of predator
     'y' : 0.5,  # predator yield on prey 
     'b' : 0.5}  # decay rate of predator


# ---plot stuff!---
x_num = rungeKutta2(balances_pred_prey, x0, t_span, p)
title = "predator-prey system"
labels = ["time", "population density"]
legend = ["prey", "predator"]
plt1, plt2, r1, r2 = get_dynamic_plots(t_span, x_num, title, labels, legend)

def update(mu=0.8, k=0.2, y=0.5, b=0.5):
    t = np.arange(0, tf+0.05, 0.05)
    prey, pred = rungeKutta2(balances_pred_prey, x0, t, {'mu':mu, 'k':k, 'y':y, 'b':b})
    
    r1[0].data_source.data = {'x': t,   'y': prey}
    r1[1].data_source.data = {'x': t,   'y': pred}
    r2.data_source.data    = {'x': prey,'y': pred}
    push_notebook()

interact(update, mu=(0,1,0.005), k=(0,1,0.005), y=(0,1,0.05), b=(0,1,0.05)) 

interactive(children=(FloatSlider(value=0.8, description='mu', max=1.0, step=0.005), FloatSlider(value=0.2, description='k', max=1.0, step=0.005), FloatSlider(value=0.5, description='y', max=1.0, step=0.05), FloatSlider(value=0.5, description='b', max=1.0, step=0.05), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

## What would happen if we add diffusion?

We already know, that if we can rewrite the system of some nonlinear ode's $\dot{\textbf{x}} = f(\textbf{x}, p)$ in the linearized form $\dot{\textbf{x}} = \textbf{A}^*\textbf{x}$, then the eigenvalues of $\textbf{A}^*$-matrix can tell us how the system will behave at some point in time, around which it was linearized. 

Can we apply the same thinking to the systems with diffusion $\dot{\textbf{x}} = D\nabla^2 \textbf{x} + f(\textbf{x}, p)$? Absolutely! The idea is the same: we need to rewrite the system $\dot{\textbf{x}} = D\nabla^2 \textbf{x} + f(\textbf{x}, p)$ in the form $\tilde{\dot{\textbf{x}}} = \tilde{\textbf{A}}\tilde{\textbf{x}}$ ($\tilde{\textbf{x}}$ can be some kind of transforms of the original $\textbf{x}$) and check the eigenvalues of the resulting $\tilde{\textbf{A}}$-matrix! Let's see how we can do it for the predator-prey system from the previous example:

$$ \begin{cases} 
   \frac{dx_{prey}}{dt} = D_{prey}\nabla^2 x_{prey} + \mu x_{prey} - \frac{k}{Y} x_{prey}x_{pred} \\ 
   \frac{dx_{prey}}{dt} = D_{pred}\nabla^2 x_{pred} + k x_{prey}x_{pred} - b x_{pred} 
   \end{cases} \rightarrow \
   \begin{bmatrix}\frac{dx_{prey}}{dt} \\ \frac{dx_{pred}}{dt} \end{bmatrix} = \
   \begin{bmatrix} D_{prey} & 0 \\ 0 & D_{pred} \end{bmatrix} \cdot \
   \begin{bmatrix} \nabla^2 x_{prey} \\ \nabla^2 x_{pred} \end{bmatrix} + \
   \begin{bmatrix} \mu - \frac{k}{Y} x_{pred} & -\frac{k}{Y} x_{prey} \\
                   k x_{pred} & k x_{prey} - b \end{bmatrix} \cdot 
   \begin{bmatrix} x_{prey} \\ x_{pred} \end{bmatrix}$$ 
   
Err... ok... So how exactly do we deal with $\begin{bmatrix} \nabla^2 x_{prey} \\ \nabla^2 x_{pred} \end{bmatrix}$?

The trick that we need to use here involves remembering that $x_{prey}$ and $x_{pred}$ are just functions, and, as any other functions, they can be represented as weighted sums of sine-waves with set frequencies:

$$ x = \int_{-\infty}^{\infty} \tilde{x}_{n}(cos(2\pi nt) + i \text{ }sin(2\pi nt))dn =  \
       \int_{-\infty}^{\infty} \tilde{x}_{n} e^{i \text{ } 2 \pi n t}dn $$
       
where $n$ are frequencies, which we choose ourselves, and $\tilde{x}_{n}$ are the weights (amplitudes) of corresponding frequencies. 

To approximate the original $x$'s _perfectly_, we'd need infinitely many sine-waves, with frequencies ranging from $-\infty$ to $+\infty$. But in practice, to approximate $x$ _well_, high but finite number of frequencies will suffice. That's exactly the idea behind [Fourier transform](...).

It might not be very clear, how Fourier transform can help us linearize the system. If anything, it seems to be obfuscating things even more... Even though it might seem this way, we're, in fact, finally about to simlify things: the integral will help us to cancel out the derivatives in $\begin{bmatrix} \nabla^2 x_{prey} \\ \nabla^2 x_{pred} \end{bmatrix}$! 

Let's plug in $\int_{-\infty}^{\infty} \tilde{x}_{n} e^{i \text{ } 2 \pi n t}dn $ 



chaos: http://www.mdpi.com/2079-8954/4/4/37/htm

thesis on reaction-diffusion: http://hantz.web.elte.hu/cikkfile/hantzth.pdf

## Finally: proper Reaction-Diffusion systems



Classic predator-prey system nicely describes, how different species affect each other at different points in time, but it completely ignores the spacial component. Or, acutally, it implicitly assumes that at any point in time each species is homogenously distributed over the space. This is a valid assumption for "well-stirred" systems, where each species can change its position in space so quick, that it doesn't really have any effect on dynamics (we'll leave answering "what's quick enough" for later). But what about all the other not-so-well-stirred systems, where the time it takes for a species to diffuse from point _A_ to point _B_ can no longer be ignored? 

In mathematical jargon the systems, that acknowledge both local interaction (__reaction__) between the species and their __diffusion__ in space, are unoriginallly called __Reaction-Diffusion__ systems. And yes, you'll need to use a bit more complex math to describe and analyse such systems. But in return you'll open up the whole new dimension of bizzare patterns and complex behaviours! Totally worth all the extra effort! Here are some inspiring examples:  
